#### Adaptive Cost Encoding (ACE)

In [25]:
from qiskit import Aer, execute
import numpy as np

In [26]:
from qiskit.circuit import ParameterVector

In [27]:
from qiskit import QuantumCircuit
from math import log2, ceil

In [28]:
def get_circuit(nq, n_layers):
  theta = ParameterVector('θ', length=nq*n_layers)
  qc = QuantumCircuit(nq)
  qc.h(range(nq))

  for layer_i in range(n_layers):
    # if layer_i%2:
    for qubit_i in range(nq - 1):
      qc.cx(qubit_i, (qubit_i + 1)%nq)
    for qubit_i in range(nq):
      qc.ry(theta[(nq*layer_i)+qubit_i], qubit_i)
  return qc

In [29]:
def get_projectors(probabilities, n_c):
  P = [0] * n_c
  P1 = [0] * n_c
  for k, v in probabilities.items():
    index = int(k[1:], 2)
    P[index] += v
    if k[0] == '1':
      P1[index] += v
  return P, P1

def objective_value(x: np.ndarray, w: np.ndarray) -> float:
    cost = 0
    for i in range(len(x)):
        for j in range(len(x)):
            cost = cost + w[i,j]*x[i]*(1-x[j])
    return cost

def get_final_measurement_binary_string(circuit, params):
  working_circuit = circuit.copy()
  # Apply measurements
  working_circuit.measure_all()
  # Bind the parameters to the circuit
  bound_circuit = working_circuit.assign_parameters(params)
  # Run the circuit on a simulator
  simulator = Aer.get_backend('qasm_simulator')
  job = execute(bound_circuit, simulator, shots=1024)
  result = job.result()
  counts = result.get_counts()
  # Compute the probabilities of the states
  probabilities = {state: counts[state] / 1024 for state in counts}
  return probabilities

def decode_probabilities(probabilities):
  binary_solution = []
  n_r = len(list(probabilities.keys())[0])-1
  n_c = 2**(n_r)
  for i in range(n_c):
    if '0' + format(i, 'b').zfill(n_r) in probabilities and '1' + format(i, 'b').zfill(n_r) in probabilities:
      if probabilities['0' + format(i, 'b').zfill(n_r)] > probabilities['1' + format(i, 'b').zfill(n_r)]:
        binary_solution.append(0)
      else:
        binary_solution.append(1)
    elif '0' + format(i, 'b').zfill(n_r) in probabilities:
      binary_solution.append(0)
    elif '1' + format(i, 'b').zfill(n_r) in probabilities:
      binary_solution.append(1)
  return binary_solution

def decode_binary_string(x, height, width):
  mask = np.zeros([height, width])
  for index,segment in enumerate(x):
    mask[index//width,index%width]=segment
  return mask

In [30]:
def evaluate_mincut_cost(params, circuit, w):
  global optimization_iteration_count
  global n_shots
  global best_cost
  global best_cost_binary_solution
  optimization_iteration_count += 1
  working_circuit = circuit.copy()

  # Apply measurements
  working_circuit.measure_all()

  # Bind the parameters to the circuit
  bound_circuit = working_circuit.assign_parameters(params)

  # Run the circuit on a simulator
  simulator = Aer.get_backend('qasm_simulator')
  job = execute(bound_circuit, simulator, shots=n_shots)
  result = job.result()
  counts = result.get_counts()

  probabilities = {state: counts[state] / n_shots for state in counts}
  n_c = 2**(len(list(probabilities.keys())[0])-1)
  P, P1 = get_projectors(probabilities, n_c)

  if 0 in P:
    return 100000

  binary_solution = decode_probabilities(probabilities)
  cost = objective_value(binary_solution, w)
  if cost < best_cost:
    best_cost = cost
    best_cost_binary_solution = binary_solution

  print(f'@ Iteration {optimization_iteration_count} Cost :',np.round(cost,2))
  print(f'Best Cost Found:',np.round(best_cost,2),"\n")
  return cost

In [31]:
# x_1 = 'basis state of the ancilla qubit whose register qubits are in the state (00) with high probability' = 1
# x_2 = 'basis state of the ancilla qubit whose register qubits are in the state (01) with high probability' = 1
# x_3 = 'basis state of the ancilla qubit whose register qubits are in the state (10) with high probability' = 0
# x_4 = 'basis state of the ancilla qubit whose register qubits are in the state (11) with high probability' = 0

In [32]:
def adaptive_cost_encoding(G, initial_params, n_layers = 1, max_iter = 2000, optimizer_method = 'COBYLA'):
  w = nx.adjacency_matrix(G).todense()
  max_cut = Maxcut(-w)
  qp = max_cut.to_quadratic_program()
  linear = qp.objective.linear.coefficients.toarray(order=None, out=None)
  quadratic = qp.objective.quadratic.coefficients.toarray(order=None, out=None)
  linear = {int(idx):-round(value,2) for idx,value in enumerate(linear[0])}
  quadratic = {(int(iy),int(ix)):-quadratic[iy, ix] for iy, ix in np.ndindex(quadratic.shape) if iy<ix and abs(quadratic[iy, ix])!=0}
  nc = len(linear)
  nr = ceil(log2(nc))
  nq = nr + 1
  qc = get_circuit(nq, n_layers)
  global optimization_iteration_count
  global best_cost
  global best_cost_binary_solution

  optimization_iteration_count = 0
  options = {}
  optimization_result = minimize(
      fun=evaluate_mincut_cost,
      x0=initial_params,
      args=(qc, w),
      method=optimizer_method,
      options=options)

  minimization_cost = optimization_result.fun
  return optimization_result.success, best_cost_binary_solution, minimization_cost, best_cost


In [33]:
from scipy.optimize import differential_evolution

In [35]:
def adaptive_cost_encoding_de(G, initial_params, n_layers = 1, max_iter = 200, optimizer_method = 'COBYLA'):
  w = nx.adjacency_matrix(G).todense()
  max_cut = Maxcut(-w)
  qp = max_cut.to_quadratic_program()
  linear = qp.objective.linear.coefficients.toarray(order=None, out=None)
  quadratic = qp.objective.quadratic.coefficients.toarray(order=None, out=None)
  linear = {int(idx):-round(value,2) for idx,value in enumerate(linear[0])}
  quadratic = {(int(iy),int(ix)):-quadratic[iy, ix] for iy, ix in np.ndindex(quadratic.shape) if iy<ix and abs(quadratic[iy, ix])!=0}
  nc = len(linear)
  nr = ceil(log2(nc))
  nq = nr + 1
  qc = get_circuit(nq, n_layers)
  global best_cost
  global best_cost_binary_solution
  optimization_iteration_count = 0
  
  optimization_result = differential_evolution(
      func=evaluate_mincut_cost,
      args = (qc, w),
      bounds=tuple([(-np.pi, np.pi) for _ in range(len(initial_params))]),
      )
  minimization_cost = optimization_result.fun
  return optimization_result.success, best_cost_binary_solution, minimization_cost, best_cost


#### Experiments for Minimal Encoding

In [38]:
base_path = './'

n_shots = 65536

optimization_max_iter = 10000
optimization_iteration_count = 0

start_layers = 1
max_layers = 1
initial_params_seed = 123
scipy_optimizer_methods = ["COBYLA", "Powell", "CG", "BFGS", "L-BFGS-B", "SLSQP"]
# scipy_optimizer_methods = ["Differential_Evolution"]


heights = [2,4,8]

seeds = [111,222,333,444,555]

[444]

In [180]:
for seed in seeds:
  report_filename = base_path + 'AncillaBasisStateEncoding_newCost_' +  str(seed) + '_' + str(n_shots) + '.txt'
  for height in heights:
    width = height
    print(f'height: {height}, width: {width}, n: {height*width}')
    np.random.seed(seed=seed)
    G, image = generate_problem_instance(height, width)
    print("Image Generated: ",image)
    for scipy_optimizer_method in scipy_optimizer_methods:
      print("Maximum number of layers :", max_layers)
      for n_layers in range(start_layers, max_layers+1,1):
        best_cost = 1000000
        best_cost_binary_solution = [0] * (height*width)
        nc = len(G.nodes())
        nr = ceil(log2(nc))
        nq = nr + 1
        initial_params = np.random.uniform(low=-np.pi, high=np.pi, size=nq*n_layers)
        print(f"Executing QC with {n_layers} layers and {scipy_optimizer_method} optimizer for {height}*{height} image.")
        # try:
        start_time = time.time()
        success_flag, minimal_encoding_solution, minimal_encoding_value, minimal_encoding_cut_value = adaptive_cost_encoding_de(G,
                                                                                                                         initial_params,
                                                                                                                         n_layers = n_layers,
                                                                                                                         max_iter = optimization_max_iter,
                                                                                                                         optimizer_method = scipy_optimizer_method)
        minimal_encoding_tte = (time.time() - start_time)
        print("New NISQ done for",scipy_optimizer_method,"optimizer with a success status :", success_flag)
        print(f"Appending the results of {height}*{height} image using QC with {n_layers} layers and {scipy_optimizer_method} optimizer.")
        row = []
        row.append(int(G.number_of_nodes()))
        row.append(int(height))
        row.append(int(width))
        row.append(success_flag)
        row.append(''.join(map(str, map(int, (minimal_encoding_solution)))))
        row.append(np.round(minimal_encoding_tte,6))
        row.append(n_layers)
        row.append(np.round(minimal_encoding_cut_value,4))
        row.append(np.round(minimal_encoding_value,4))
        row.append(optimization_iteration_count)
        row.append(scipy_optimizer_method)
        report_file_obj = open(os.path.join(report_filename),'a+')
        report_file_obj.write('__'.join(map(str,row))+'\n')
        report_file_obj.close()
    print('\n')

height: 4, width: 4, n: 16
Image Generated:  [[0.83936105 0.82129497 0.64220716 0.66722262]
 [0.03913991 0.06567239 0.27650064 0.3163605 ]
 [0.19359241 0.19709288 0.84920429 0.84235809]
 [0.34736473 0.7397423  0.49340914 0.47301173]]
Maximum number of layers : 1
Executing QC with 1 layers and Differential_Evolution optimizer for 4*4 image.
@ Iteration 1 Cost : 0.0
Best Cost Found: 0.0 

@ Iteration 3 Cost : 0.0
Best Cost Found: 0.0 

@ Iteration 4 Cost : 0.0
Best Cost Found: 0.0 

@ Iteration 5 Cost : 7.0200000000000005
Best Cost Found: 0.0 

@ Iteration 6 Cost : 0.0
Best Cost Found: 0.0 

@ Iteration 7 Cost : 0.0
Best Cost Found: 0.0 

@ Iteration 8 Cost : 0.0
Best Cost Found: 0.0 

@ Iteration 10 Cost : 0.0
Best Cost Found: 0.0 

@ Iteration 11 Cost : 0.0
Best Cost Found: 0.0 

@ Iteration 17 Cost : 0.0
Best Cost Found: 0.0 

@ Iteration 18 Cost : 0.0
Best Cost Found: 0.0 

@ Iteration 20 Cost : 0.0
Best Cost Found: 0.0 

@ Iteration 21 Cost : 0.0
Best Cost Found: 0.0 

@ Iteration 2

#### Gurobi Solver

In [42]:
def gurobi_mincut_solver(G, **kwargs):
  w = -1 * nx.adjacency_matrix(G).todense()
  max_cut = Maxcut(w)
  qp = max_cut.to_quadratic_program()
  linear = qp.objective.linear.coefficients.toarray(order=None, out=None)
  quadratic = qp.objective.quadratic.coefficients.toarray(order=None, out=None)

  linear = {int(idx):-round(value,2) for idx,value in enumerate(linear[0])}
  quadratic = {(int(iy),int(ix)):-quadratic[iy, ix] for iy, ix in np.ndindex(quadratic.shape) if iy<ix and abs(quadratic[iy, ix])!=0}

  qubo_matrix = np.zeros([len(linear),len(linear)])
  for key,value in linear.items():
    qubo_matrix[int(key),int(key)] = value
  for key,value in quadratic.items():
    qubo_matrix[int(key[0]),int(key[1])] = value/2
    qubo_matrix[int(key[1]),int(key[0])] = value/2

  #size of the QUBO matrix
  n = qubo_matrix.shape[0]
  model = gp.Model()

  #initialize binary variables
  x = model.addVars(n, vtype=GRB.BINARY)

  #objective function to minimize the QUBO matrix
  obj_expr = gp.quicksum(qubo_matrix[i, j] * x[i] * x[j] for i in range(n) for j in range(n))
  model.setObjective(obj_expr)

  model.setParam('OutputFlag', 0)

  model.optimize()

  if model.status == GRB.OPTIMAL:
    solution = [int(x[i].X) for i in range(n)]
    binary_string = ''.join(str(bit) for bit in solution)
    return binary_string, model.objVal
  else:
    return None, None